# Imports

In [1]:
from pystock.portfolio import Portfolio, Stock
from pystock.fff import FamaFrenchFactors
from pystock.frontier.frontier import EfficientFrontier
import pystock
import os
import plotly.io as pio

print(pystock.__version__)
pio.renderers.default = "notebook"
pio.templates.default = "plotly_dark"

0.3.0


# How to use `frontier`

There are a few steps involved:
1. Create a `Portfolio`
2. Make sure that the data of stocks in the `Portfolio` is loaded 
3. (Optional) You also need to calculate FFF parameters if you want to use FFF3 or FFF5 models.
4. That's all!

## Creating a `Portfolio`

In [2]:
stock_dir = "Data"
index_dir = "Data"

In [3]:
apple = Stock(directory=os.path.join(stock_dir, "AAPL.csv"), name="Apple")
google = Stock(directory=os.path.join(stock_dir, "GOOGL.csv"), name="Google")
tesla = Stock(directory=os.path.join(stock_dir, "TSLA.csv"), name="Tesla")
microsoft = Stock(directory=os.path.join(stock_dir, "MSFT.csv"), name="Microsoft")

In [4]:
stocks = [apple, google, tesla, microsoft]
benchmark_dir = os.path.join(index_dir, "GSPC.csv")
p = Portfolio(benchmark_dir=benchmark_dir, benchmark_name="S&P 500")
p

Portfolio(S&P 500, [])

In [5]:
start_date = "2012-01-01"
end_date = "2022-12-01"
frequency = "M"
p.add_stocks(stocks, load_data=True, start_date=start_date, end_date=end_date, frequency=frequency, columns=["Close"], rename_cols=["Close"])
p

Portfolio(S&P 500, ['Apple', 'Google', 'Tesla', 'Microsoft'])

In [6]:
for stock, name in p:
    print(stock.loaded, name)

False S&P 500
True Apple
True Google
True Tesla
True Microsoft


Now load the index

In [7]:
p.load_benchmark(start_date=start_date, end_date=end_date, frequency=frequency, columns=["Close"], rename_cols=["Close"])

In [8]:
for stock, name in p:
    print(stock.loaded, name)

True S&P 500
True Apple
True Google
True Tesla
True Microsoft


In [9]:
ef = EfficientFrontier(portfolio=p)

In [10]:
p.summary()

Portfolio Summary
*****************

The Portfolio
Portfolio with benchmark S&P 500 and stocks ['Apple', 'Google', 'Tesla', 'Microsoft']

Here are the summary of stocks in the portfolio:
+----+-----------+-----------------------+----------------------+------------+----------+----------+
|    | Stock     |   Monthly_Mean_Return |   Monthly_Return_STD |      Alpha |     Beta |   Weight |
|----+-----------+-----------------------+----------------------+------------+----------+----------|
|  0 | Apple     |             0.0203446 |            0.0810776 | 0.008545   | 1.22705  |     0.25 |
|  1 | Google    |             0.0170734 |            0.0645873 | 0.00705479 | 1.04185  |     0.25 |
|  2 | Tesla     |             0.0502608 |            0.182803  | 0.0336704  | 1.72526  |     0.25 |
|  3 | Microsoft |             0.0202463 |            0.060776  | 0.010973   | 0.964346 |     0.25 |
+----+-----------+-----------------------+----------------------+------------+----------+----------+

The 

In [11]:
p.calculate_fff_params(factors=5, frequency="M", directory="Data", download=False)

Here are the FFF parameters
+----------------+-------------+-------------+------------+-------------+
| Coefficients   |       Apple |      Google |      Tesla |   Microsoft |
|----------------+-------------+-------------+------------+-------------|
| const          |  0.00551378 |  0.00694344 |  0.0341999 |  0.00970946 |
| Mkt-RF         |  1.19761    |  1.00289    |  1.87135   |  0.994033   |
| SMB            | -0.25864    | -0.562694   | -0.379263  | -0.776582   |
| HML            | -0.51356    |  0.202691   | -0.610234  |  0.0184878  |
| RMW            |  0.75083    | -0.0688105  | -1.45574   | -0.103125   |
| CMA            | -0.181558   | -0.892375   | -0.497976  | -0.548657   |
| rf             |  1          |  1          |  1         |  1          |
+----------------+-------------+-------------+------------+-------------+


In [12]:
fig = ef.plot_frontier(short=True, model="capm")

Calculating returns: 100%|██████████| 8000/8000 [00:00<00:00, 13383.36it/s]


In [13]:
fig = ef.plot_frontier(short=True, model="sim")

Calculating returns: 100%|██████████| 8000/8000 [00:00<00:00, 10346.67it/s]


## Using the FFF Models

First, download the FFF params if you don't have this data in your direcory.

In [14]:
ff = FamaFrenchFactors()

ff.download(frequency=frequency, factors=5, directory="data")

Download complete. File saved as data/fff_monthly_5_factors.csv
Use load() to load the file as a pandas dataframe.


'data/fff_monthly_5_factors.csv'

Now, use `Portfolio.calculate_fff_params` to calculate the params using the data you just downloaded.

In [15]:
p.calculate_fff_params(factors=5, frequency=frequency, directory="data", download=False)

Here are the FFF parameters
+----------------+-------------+-------------+-----------+-------------+
| Coefficients   |       Apple |      Google |     Tesla |   Microsoft |
|----------------+-------------+-------------+-----------+-------------|
| const          |  0.00551057 |  0.00693377 |  0.034192 |  0.00970534 |
| Mkt-RF         |  1.1975     |  1.00254    |  1.87141  |  0.993697   |
| SMB            | -0.25978    | -0.562751   | -0.379262 | -0.776818   |
| HML            | -0.513378   |  0.203187   | -0.611613 |  0.0190261  |
| RMW            |  0.74824    | -0.0696005  | -1.45656  | -0.104464   |
| CMA            | -0.18071    | -0.894186   | -0.496061 | -0.550016   |
| rf             |  1          |  1          |  1        |  1          |
+----------------+-------------+-------------+-----------+-------------+


Great! Now you are ready.

In [16]:
fig = ef.plot_frontier(short=False, model="fff3")

Calculating returns: 100%|██████████| 8000/8000 [00:07<00:00, 1030.84it/s]


In [17]:
fig = ef.plot_frontier(short=True, model="fff5")

Calculating returns: 100%|██████████| 8000/8000 [00:01<00:00, 4440.01it/s]
